In [93]:
import pandas as pd
import numpy as np
import ast

In [94]:
df = pd.read_csv('all_tag.csv')
df.nunique()

appid              51951
name               51714
developer          32644
publisher          27964
score_rank             3
positive            4492
negative            2264
userscore             33
owners                13
average_forever     2226
average_2weeks       612
median_forever      1878
median_2weeks        627
price                413
initialprice         194
discount              74
ccu                 1107
languages           8297
genre               1740
tags               49261
dtype: int64

## drop_duplicates ด้วย appid

In [95]:
# drop appid ซ้ำ
df = pd.read_csv('all_tag.csv')
df = df.drop_duplicates(subset=['appid'], keep='first')
df.reset_index(drop= True, inplace= True)
df.nunique()

appid              51951
name               51714
developer          32639
publisher          27949
score_rank             3
positive            4475
negative            2259
userscore             33
owners                13
average_forever     2206
average_2weeks       611
median_forever      1858
median_2weeks        624
price                410
initialprice         194
discount              73
ccu                 1098
languages           8290
genre               1734
tags               49117
dtype: int64

## เปลี่ยน genre ,tag เป็น list

In [98]:
# เปลี่ยน genre ,tag เป็น list
appid = df["appid"]
genre_list = []
tag_list = []
missing_pos = []
for i in range(len(df)):
    genre = str((df["genre"])[i]).split(', ')
    genre_list.append(genre) 
    tag_str = df['tags'][i]

    if tag_str != '[]' :
        tag_dict = ast.literal_eval(tag_str)
        tag = list(tag_dict.keys())
        
    else:
        tag = ["nan"]
        missing_pos.append(i)

    tag_list.append(tag)

    # d.update({'appid': appid})
    # d.update({'genre': genre_list})
    # d.update({'tags': tag_list})
    
    # df = pd.DataFrame(data= d, index= None)

df['genre'] = genre_list
df['tags'] = tag_list



In [100]:
df.to_csv('data\All_feature.csv', index= False)

### drop feature ที่ไม่ใช้

In [101]:
# drop feature
df_drop = df.drop(columns=[ 'developer', 'publisher', 'score_rank','average_forever', 'average_2weeks',
       'median_forever', 'median_2weeks', 'userscore', 'languages','ccu','discount', 'owners'])
df_drop.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 51951 entries, 0 to 51950
Data columns (total 8 columns):
 #   Column        Non-Null Count  Dtype  
---  ------        --------------  -----  
 0   appid         51951 non-null  int64  
 1   name          51941 non-null  object 
 2   positive      51951 non-null  int64  
 3   negative      51951 non-null  int64  
 4   price         51922 non-null  float64
 5   initialprice  51929 non-null  float64
 6   genre         51951 non-null  object 
 7   tags          51951 non-null  object 
dtypes: float64(2), int64(3), object(3)
memory usage: 3.2+ MB


In [102]:
df_drop.keys()

Index(['appid', 'name', 'positive', 'negative', 'price', 'initialprice',
       'genre', 'tags'],
      dtype='object')

In [103]:
df_drop.to_csv('data\usable_feature.csv', index= False)

In [104]:
game_features = df_drop[['appid', 'genre', 'tags']]
game_features.head(5)

appid                                              genre  \
0      570                   [Action, Free to Play, Strategy]   
1      730                             [Action, Free to Play]   
2   578080  [Action, Adventure, Free to Play, Massively Mu...   
3  1063730    [Action, Adventure, Massively Multiplayer, RPG]   
4      440                             [Action, Free to Play]   

                                                tags  
0  [Free to Play, MOBA, Multiplayer, Strategy, e-...  
1  [FPS, Shooter, Multiplayer, Competitive, Actio...  
2  [Survival, Shooter, Multiplayer, Battle Royale...  
3  [Massively Multiplayer, Open World, MMORPG, RP...  
4  [Free to Play, Hero Shooter, Multiplayer, FPS,...

## One Hot Encoding

In [106]:
type(df_drop['tags'][i])

list

In [107]:
u_tag = []
for i in range(len(df_drop)):
    tag_list = df_drop['tags'][i]
    for tag in tag_list:
        if tag not in u_tag:
            u_tag.append(tag)
    print(i)
print(len(u_tag))

0
1
2
3
4
5
6
7
8
9
10
11
12
13
14
15
16
17
18
19
20
21
22
23
24
25
26
27
28
29
30
31
32
33
34
35
36
37
38
39
40
41
42
43
44
45
46
47
48
49
50
51
52
53
54
55
56
57
58
59
60
61
62
63
64
65
66
67
68
69
70
71
72
73
74
75
76
77
78
79
80
81
82
83
84
85
86
87
88
89
90
91
92
93
94
95
96
97
98
99
100
101
102
103
104
105
106
107
108
109
110
111
112
113
114
115
116
117
118
119
120
121
122
123
124
125
126
127
128
129
130
131
132
133
134
135
136
137
138
139
140
141
142
143
144
145
146
147
148
149
150
151
152
153
154
155
156
157
158
159
160
161
162
163
164
165
166
167
168
169
170
171
172
173
174
175
176
177
178
179
180
181
182
183
184
185
186
187
188
189
190
191
192
193
194
195
196
197
198
199
200
201
202
203
204
205
206
207
208
209
210
211
212
213
214
215
216
217
218
219
220
221
222
223
224
225
226
227
228
229
230
231
232
233
234
235
236
237
238
239
240
241
242
243
244
245
246
247
248
249
250
251
252
253
254
255
256
257
258
259
260
261
262
263
264
265
266
267
268
269
270
271
272
273
274
275
276
27

In [108]:
zeros = np.zeros((len(df_drop), len(u_tag))) #(row, col)
np.shape(zeros)

(51951, 442)

In [109]:
ohe_df_tag = pd.DataFrame(zeros, columns= u_tag)

for game in range(len(df_drop)):
    tag_list = df_drop['tags'][game]
    for tag in tag_list:
        ohe_df_tag[tag][game] = 1
    print('-----' , game , '-----')

----- 0 -----
----- 1 -----
----- 2 -----
----- 3 -----
----- 4 -----
----- 5 -----
----- 6 -----
----- 7 -----
----- 8 -----
----- 9 -----
----- 10 -----
----- 11 -----
----- 12 -----
----- 13 -----
----- 14 -----
----- 15 -----
----- 16 -----
----- 17 -----
----- 18 -----
----- 19 -----
----- 20 -----
----- 21 -----
----- 22 -----
----- 23 -----
----- 24 -----
----- 25 -----
----- 26 -----
----- 27 -----
----- 28 -----
----- 29 -----
----- 30 -----
----- 31 -----
----- 32 -----
----- 33 -----
----- 34 -----
----- 35 -----
----- 36 -----
----- 37 -----
----- 38 -----
----- 39 -----
----- 40 -----
----- 41 -----
----- 42 -----
----- 43 -----
----- 44 -----
----- 45 -----
----- 46 -----
----- 47 -----
----- 48 -----
----- 49 -----
----- 50 -----
----- 51 -----
----- 52 -----
----- 53 -----
----- 54 -----
----- 55 -----
----- 56 -----
----- 57 -----
----- 58 -----
----- 59 -----
----- 60 -----
----- 61 -----
----- 62 -----
----- 63 -----
----- 64 -----
----- 65 -----
----- 66 -----
-----

In [115]:
ohe_df_tag.drop(columns= ['nan'], inplace= True)
np.shape(ohe_df_tag)

KeyError: "['nan'] not found in axis"

In [117]:
ohe_df_tag.to_csv('data\ohe_tags.csv')

In [118]:
u_genre = []
for i in range(len(df)):
    genre_list = df_drop['genre'][i]
    for genre in genre_list:
        if genre not in u_genre:
            u_genre.append(genre)
    print("%.2f"  %(i / len(df)*100 ))
print(len(u_genre))

0.00
0.00
0.00
0.01
0.01
0.01
0.01
0.01
0.02
0.02
0.02
0.02
0.02
0.03
0.03
0.03
0.03
0.03
0.03
0.04
0.04
0.04
0.04
0.04
0.05
0.05
0.05
0.05
0.05
0.06
0.06
0.06
0.06
0.06
0.07
0.07
0.07
0.07
0.07
0.08
0.08
0.08
0.08
0.08
0.08
0.09
0.09
0.09
0.09
0.09
0.10
0.10
0.10
0.10
0.10
0.11
0.11
0.11
0.11
0.11
0.12
0.12
0.12
0.12
0.12
0.13
0.13
0.13
0.13
0.13
0.13
0.14
0.14
0.14
0.14
0.14
0.15
0.15
0.15
0.15
0.15
0.16
0.16
0.16
0.16
0.16
0.17
0.17
0.17
0.17
0.17
0.18
0.18
0.18
0.18
0.18
0.18
0.19
0.19
0.19
0.19
0.19
0.20
0.20
0.20
0.20
0.20
0.21
0.21
0.21
0.21
0.21
0.22
0.22
0.22
0.22
0.22
0.23
0.23
0.23
0.23
0.23
0.23
0.24
0.24
0.24
0.24
0.24
0.25
0.25
0.25
0.25
0.25
0.26
0.26
0.26
0.26
0.26
0.27
0.27
0.27
0.27
0.27
0.28
0.28
0.28
0.28
0.28
0.28
0.29
0.29
0.29
0.29
0.29
0.30
0.30
0.30
0.30
0.30
0.31
0.31
0.31
0.31
0.31
0.32
0.32
0.32
0.32
0.32
0.33
0.33
0.33
0.33
0.33
0.33
0.34
0.34
0.34
0.34
0.34
0.35
0.35
0.35
0.35
0.35
0.36
0.36
0.36
0.36
0.36
0.37
0.37
0.37
0.37
0.37
0.38
0.38
0.38
0.38
0.38


In [119]:
zeros_genre = np.zeros((len(df_drop), len(u_genre))) #(row, col)
np.shape(zeros_genre)

(51951, 29)

In [120]:
ohe_df_genre = pd.DataFrame(zeros_genre, columns= u_genre)

for game in range(len(df_drop)):
    genre_list = df_drop['genre'][game]
    for genre in genre_list:
        ohe_df_genre[genre][game] = 1
    print('----- %.3f  -----'   %(game / len(df)*100 ) )

----- 0.000  -----
----- 0.002  -----
----- 0.004  -----
----- 0.006  -----
----- 0.008  -----
----- 0.010  -----
----- 0.012  -----
----- 0.013  -----
----- 0.015  -----
----- 0.017  -----
----- 0.019  -----
----- 0.021  -----
----- 0.023  -----
----- 0.025  -----
----- 0.027  -----
----- 0.029  -----
----- 0.031  -----
----- 0.033  -----
----- 0.035  -----
----- 0.037  -----
----- 0.038  -----
----- 0.040  -----
----- 0.042  -----
----- 0.044  -----
----- 0.046  -----
----- 0.048  -----
----- 0.050  -----
----- 0.052  -----
----- 0.054  -----
----- 0.056  -----
----- 0.058  -----
----- 0.060  -----
----- 0.062  -----
----- 0.064  -----
----- 0.065  -----
----- 0.067  -----
----- 0.069  -----
----- 0.071  -----
----- 0.073  -----
----- 0.075  -----
----- 0.077  -----
----- 0.079  -----
----- 0.081  -----
----- 0.083  -----
----- 0.085  -----
----- 0.087  -----
----- 0.089  -----
----- 0.090  -----
----- 0.092  -----
----- 0.094  -----
----- 0.096  -----
----- 0.098  -----
----- 0.100 

In [122]:
ohe_df_genre = ohe_df_genre.drop(columns= ['nan'])

In [123]:
ohe_df_genre.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 51951 entries, 0 to 51950
Data columns (total 28 columns):
 #   Column                 Non-Null Count  Dtype  
---  ------                 --------------  -----  
 0   Action                 51951 non-null  float64
 1   Free to Play           51951 non-null  float64
 2   Strategy               51951 non-null  float64
 3   Adventure              51951 non-null  float64
 4   Massively Multiplayer  51951 non-null  float64
 5   RPG                    51951 non-null  float64
 6   Casual                 51951 non-null  float64
 7   Indie                  51951 non-null  float64
 8   Simulation             51951 non-null  float64
 9   Early Access           51951 non-null  float64
 10  Animation & Modeling   51951 non-null  float64
 11  Design & Illustration  51951 non-null  float64
 12  Photo Editing          51951 non-null  float64
 13  Utilities              51951 non-null  float64
 14  Sports                 51951 non-null  float64
 15  Ra

In [127]:
ohe_df_genre.to_csv('data\ohe_genre.csv')

### รวมตาราง genre กับ tag

In [125]:
ohe_df_genre.keys()

Index(['Action', 'Free to Play', 'Strategy', 'Adventure',
       'Massively Multiplayer', 'RPG', 'Casual', 'Indie', 'Simulation',
       'Early Access', 'Animation & Modeling', 'Design & Illustration',
       'Photo Editing', 'Utilities', 'Sports', 'Racing', 'Video Production',
       'Audio Production', 'Game Development', 'Web Publishing', 'Violent',
       'Gore', 'Movie', 'Education', 'Software Training', 'Sexual Content',
       'Accounting', 'Nudity'],
      dtype='object')

#### เช็ค tag ซ้ำกับ genre

In [129]:
tag_to_drop = []
genre_list = list(ohe_df_genre.keys())
for tag in ohe_df_tag.keys():
    if tag in genre_list:
        tag_to_drop.append(tag)

In [133]:
ohe_df_tag = ohe_df_tag.drop(columns= tag_to_drop)

In [139]:
ohe_df_tag.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 51951 entries, 0 to 51950
Columns: 414 entries, MOBA to Masterpiece
dtypes: float64(414)
memory usage: 164.1 MB


In [143]:
ohe_df_tag.to_csv('data\Tag_unique.csv', index= False)

In [140]:
genre_tag = pd.concat([df_drop['appid'], ohe_df_genre, ohe_df_tag], axis=1)

In [142]:
genre_tag.head()

appid  Action  Free to Play  Strategy  Adventure  Massively Multiplayer  \
0      570     1.0           1.0       1.0        0.0                    0.0   
1      730     1.0           1.0       0.0        0.0                    0.0   
2   578080     1.0           1.0       0.0        1.0                    1.0   
3  1063730     1.0           0.0       0.0        1.0                    1.0   
4      440     1.0           1.0       0.0        0.0                    0.0   

   RPG  Casual  Indie  Simulation  ...  Baseball  Shop Keeper  Electronic  \
0  0.0     0.0    0.0         0.0  ...       0.0          0.0         0.0   
1  0.0     0.0    0.0         0.0  ...       0.0          0.0         0.0   
2  0.0     0.0    0.0         0.0  ...       0.0          0.0         0.0   
3  1.0     0.0    0.0         0.0  ...       0.0          0.0         0.0   
4  0.0     0.0    0.0         0.0  ...       0.0          0.0         0.0   

   Volleyball  Coding  Cricket  Instrumental Music  Rugby  8-bit Music  \
0         0.0     0.0      0.0                 0.0    0.0          0.0   
1         0.0     0.0      0.0                 0.0    0.0          0.0   
2         0.0     0.0      0.0                 0.0    0.0          0.0   
3         0.0     0.0      0.0                 0.0    0.0          0.0   
4         0.0     0.0      0.0                 0.0    0.0          0.0   

   Masterpiece  
0          0.0  
1          0.0  
2          0.0  
3          0.0  
4          0.0  

[5 rows x 443 columns]

In [144]:
genre_tag.to_csv('data\genre_tag.csv', index= False)